In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, random_split
from torchvision import transforms, models, datasets
from tqdm import tqdm
import matplotlib.pyplot as plt
from pathlib import Path
import numpy as np
from collections import Counter


In [2]:

# Set random seed for reproducibility
torch.manual_seed(42)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cpu


In [3]:

# Define data transformations
train_transforms = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.RandomHorizontalFlip(),
    transforms.RandomRotation(10),
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

val_test_transforms = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

In [4]:

# Load and split the dataset
dataset_path = Path("Dataset")
full_dataset = datasets.ImageFolder(root=dataset_path, transform=train_transforms)
num_classes = len(full_dataset.classes)

In [5]:

# Calculate class weights
class_counts = Counter([label for _, label in full_dataset.samples])
total_samples = sum(class_counts.values())
class_weights = {cls: total_samples / (len(class_counts) * count) 
                for cls, count in class_counts.items()}


In [6]:

# Convert to tensor
weight_tensor = torch.FloatTensor([class_weights[i] for i in range(num_classes)]).to(device)


In [7]:

# Calculate lengths for splits (70% train, 15% val, 15% test)
total_size = len(full_dataset)
train_size = int(0.7 * total_size)
val_size = int(0.15 * total_size)
test_size = total_size - train_size - val_size


In [8]:

# Split the dataset
train_dataset, val_dataset, test_dataset = random_split(
    full_dataset, [train_size, val_size, test_size]
)

# Update transforms for validation and test sets
val_dataset.dataset.transform = val_test_transforms
test_dataset.dataset.transform = val_test_transforms

# Create data loaders
batch_size = 32
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=4)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False, num_workers=4)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)


In [9]:

print(f"Number of training samples: {len(train_dataset)}")
print(f"Number of validation samples: {len(val_dataset)}")
print(f"Number of test samples: {len(test_dataset)}")
print(f"Number of classes: {num_classes}")


Number of training samples: 11487
Number of validation samples: 2461
Number of test samples: 2462
Number of classes: 151


In [10]:

# Print class distribution and weights
print("\nClass distribution and weights:")
for cls_idx, cls_name in enumerate(full_dataset.classes):
    count = class_counts[cls_idx]
    weight = class_weights[cls_idx]
    print(f"{cls_name}: {count} samples, weight = {weight:.2f}")



Class distribution and weights:
Abra: 59 samples, weight = 1.84
Aerodactyl: 107 samples, weight = 1.02
Alakazam: 68 samples, weight = 1.60
Arbok: 112 samples, weight = 0.97
Arcanine: 139 samples, weight = 0.78
Articuno: 125 samples, weight = 0.87
Beedrill: 125 samples, weight = 0.87
Bellsprout: 115 samples, weight = 0.95
Blastoise: 128 samples, weight = 0.85
Bulbasaur: 182 samples, weight = 0.60
Butterfree: 157 samples, weight = 0.69
Caterpie: 133 samples, weight = 0.82
Chansey: 119 samples, weight = 0.91
Charizard: 105 samples, weight = 1.04
Charmander: 153 samples, weight = 0.71
Charmeleon: 124 samples, weight = 0.88
Clefable: 97 samples, weight = 1.12
Clefairy: 88 samples, weight = 1.23
Cloyster: 89 samples, weight = 1.22
Cubone: 147 samples, weight = 0.74
Dewgong: 100 samples, weight = 1.09
Diglett: 85 samples, weight = 1.28
Ditto: 84 samples, weight = 1.29
Dodrio: 93 samples, weight = 1.17
Doduo: 76 samples, weight = 1.43
Dragonair: 104 samples, weight = 1.04
Dragonite: 122 sampl

In [11]:

# Load pre-trained VGG16 model
model = models.vgg16(pretrained=True)


/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=VGG16_Weights.IMAGENET1K_V1`. You can also use `weights=VGG16_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [12]:

# Freeze feature layers
for param in model.features.parameters():
    param.requires_grad = False

In [13]:

# Modify classifier for our number of classes
model.classifier[6] = nn.Linear(4096, num_classes)
model = model.to(device)

# Define weighted loss function and optimizer
criterion = nn.CrossEntropyLoss(weight=weight_tensor)
optimizer = optim.Adam(model.parameters(), lr=0.001)
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=3, verbose=True)


/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/torch/optim/lr_scheduler.py:62: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn(


In [14]:

# Training function
def train_epoch(model, loader, criterion, optimizer):
    model.train()
    running_loss = 0.0
    correct = 0
    total = 0
    
    progress_bar = tqdm(loader, desc="Training")
    for inputs, labels in progress_bar:
        inputs, labels = inputs.to(device), labels.to(device)
        
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item()
        _, predicted = outputs.max(1)
        total += labels.size(0)
        correct += predicted.eq(labels).sum().item()
        
        progress_bar.set_postfix({
            'loss': f'{running_loss/len(progress_bar):.3f}',
            'acc': f'{100.*correct/total:.2f}%'
        })
    
    return running_loss/len(loader), 100.*correct/total

In [15]:

# Validation function
def validate(model, loader, criterion):
    model.eval()
    running_loss = 0.0
    correct = 0
    total = 0
    
    # Add per-class accuracy tracking
    class_correct = torch.zeros(num_classes).to(device)
    class_total = torch.zeros(num_classes).to(device)
    
    with torch.no_grad():
        progress_bar = tqdm(loader, desc="Validating")
        for inputs, labels in progress_bar:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            
            running_loss += loss.item()
            _, predicted = outputs.max(1)
            total += labels.size(0)
            correct += predicted.eq(labels).sum().item()
            
            # Update per-class accuracy
            for label_idx in range(num_classes):
                mask = labels == label_idx
                class_correct[label_idx] += predicted[mask].eq(labels[mask]).sum().item()
                class_total[label_idx] += mask.sum().item()
            
            progress_bar.set_postfix({
                'loss': f'{running_loss/len(progress_bar):.3f}',
                'acc': f'{100.*correct/total:.2f}%'
            })
    
    # Print per-class accuracy
    print("\nPer-class accuracy:")
    for i in range(num_classes):
        if class_total[i] > 0:
            class_acc = 100. * class_correct[i] / class_total[i]
            print(f'{full_dataset.classes[i]}: {class_acc:.2f}%')
    
    return running_loss/len(loader), 100.*correct/total


In [16]:
import json
from datetime import datetime

def save_metrics(metrics, filename):
    with open(filename, 'w') as f:
        json.dump(metrics, f)

def load_metrics(filename):
    try:
        with open(filename, 'r') as f:
            return json.load(f)
    except FileNotFoundError:
        return {
            'train_losses': [], 
            'train_accs': [],
            'val_losses': [], 
            'val_accs': [],
            'epochs_completed': 0
        }

In [17]:


# training loop section
metrics_file = 'checkpoints/training_metrics.json'
checkpoint_file = 'checkpoints/training_checkpoint.pth'
metrics = load_metrics(metrics_file)

train_losses = metrics['train_losses']
train_accs = metrics['train_accs']
val_losses = metrics['val_losses']
val_accs = metrics['val_accs']
start_epoch = metrics['epochs_completed']
best_val_acc = max(metrics['val_accs']) if metrics['val_accs'] else 0

# best_model_path = 'best_pokemon_classifier.pth'

num_epochs = 10
print("Starting training...")
for epoch in range(start_epoch, num_epochs):
    print(f"\nEpoch {epoch+1}/{num_epochs}")
    
    # Train
    train_loss, train_acc = train_epoch(model, train_loader, criterion, optimizer)
    train_losses.append(train_loss)
    train_accs.append(train_acc)
    
    # Validate
    val_loss, val_acc = validate(model, val_loader, criterion)
    val_losses.append(val_loss)
    val_accs.append(val_acc)
    
    # Update learning rate
    scheduler.step(val_loss)
    
    # Save checkpoint and metrics
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        checkpoint = {
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'scheduler_state_dict': scheduler.state_dict(),
            'best_val_acc': best_val_acc
        }
        torch.save(checkpoint, checkpoint_file)
        print(f"New best model saved with validation accuracy: {val_acc:.2f}% at epoch {epoch+1} to {checkpoint_file}")
    
    metrics = {
        'train_losses': train_losses,
        'train_accs': train_accs,
        'val_losses': val_losses,
        'val_accs': val_accs,
        'epochs_completed': epoch + 1
    }
    save_metrics(metrics, metrics_file)
    
    print(f"Train Loss: {train_loss:.4f}, Train Acc: {train_acc:.2f}%")
    print(f"Val Loss: {val_loss:.4f}, Val Acc: {val_acc:.2f}%")


Starting training...

Epoch 3/10


Training:   1%|          | 4/359 [00:07<10:40,  1.80s/it, loss=0.058, acc=2.34%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:   6%|▌         | 22/359 [00:40<10:13,  1.82s/it, loss=0.331, acc=1.56%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:   9%|▉         | 33/359 [01:00<10:11,  1.88s/it, loss=0.489, acc=1.61%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  40%|███▉      | 143/359 [04:35<06:16,  1.74s/it, loss=2.028, acc=2.05%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:98


Per-class accuracy:
Abra: 0.00%
Aerodactyl: 0.00%
Alakazam: 16.67%
Arbok: 0.00%
Arcanine: 22.22%
Articuno: 45.83%
Beedrill: 22.73%
Bellsprout: 0.00%
Blastoise: 0.00%
Bulbasaur: 7.41%
Butterfree: 53.33%
Caterpie: 0.00%
Chansey: 0.00%
Charizard: 0.00%
Charmander: 0.00%
Charmeleon: 0.00%
Clefable: 69.23%
Clefairy: 0.00%
Cloyster: 0.00%
Cubone: 0.00%
Dewgong: 0.00%
Diglett: 69.23%
Ditto: 50.00%
Dodrio: 25.00%
Doduo: 58.33%
Dragonair: 42.86%
Dragonite: 0.00%
Dratini: 0.00%
Drowzee: 0.00%
Dugtrio: 4.35%
Eevee: 0.00%
Ekans: 45.45%
Electabuzz: 12.50%
Electrode: 90.00%
Exeggcute: 11.11%
Exeggutor: 0.00%
Farfetch'd: 0.00%
Fearow: 16.67%
Flareon: 19.23%
Gastly: 60.00%
Gengar: 0.00%
Geodude: 0.00%
Gloom: 0.00%
Golbat: 41.67%
Goldeen: 0.00%
Golduck: 78.57%
Golem: 0.00%
Graveler: 14.29%
Grimer: 0.00%
Growlithe: 0.00%
Gyarados: 0.00%
Haunter: 0.00%
Hitmonchan: 0.00%
Hitmonlee: 0.00%
Horsea: 0.00%
Hypno: 0.00%
Ivysaur: 21.43%
Jigglypuff: 21.05%
Jolteon: 53.85%
Jynx: 0.00%
Kabuto: 0.00%
Kabutops: 6.25

Training:   3%|▎         | 10/359 [00:21<12:06,  2.08s/it, loss=0.124, acc=12.19%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  11%|█         | 39/359 [01:22<11:16,  2.11s/it, loss=0.494, acc=10.50%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  16%|█▌        | 57/359 [01:59<10:18,  2.05s/it, loss=0.717, acc=11.68%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  78%|███████▊  | 280/359 [09:04<02:23,  1.82s/it, loss=3.351, acc=15.49%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.


Per-class accuracy:
Abra: 0.00%
Aerodactyl: 0.00%
Alakazam: 0.00%
Arbok: 9.09%
Arcanine: 11.11%
Articuno: 29.17%
Beedrill: 40.91%
Bellsprout: 82.61%
Blastoise: 25.00%
Bulbasaur: 40.74%
Butterfree: 83.33%
Caterpie: 21.05%
Chansey: 42.86%
Charizard: 0.00%
Charmander: 40.00%
Charmeleon: 0.00%
Clefable: 76.92%
Clefairy: 0.00%
Cloyster: 0.00%
Cubone: 16.67%
Dewgong: 35.71%
Diglett: 69.23%
Ditto: 83.33%
Dodrio: 58.33%
Doduo: 58.33%
Dragonair: 85.71%
Dragonite: 0.00%
Dratini: 17.65%
Drowzee: 0.00%
Dugtrio: 65.22%
Eevee: 42.11%
Ekans: 72.73%
Electabuzz: 6.25%
Electrode: 90.00%
Exeggcute: 66.67%
Exeggutor: 52.94%
Farfetch'd: 0.00%
Fearow: 33.33%
Flareon: 11.54%
Gastly: 40.00%
Gengar: 28.57%
Geodude: 0.00%
Gloom: 100.00%
Golbat: 50.00%
Goldeen: 0.00%
Golduck: 14.29%
Golem: 0.00%
Graveler: 50.00%
Grimer: 52.94%
Growlithe: 0.00%
Gyarados: 0.00%
Haunter: 58.82%
Hitmonchan: 7.69%
Hitmonlee: 0.00%
Horsea: 48.15%
Hypno: 50.00%
Ivysaur: 78.57%
Jigglypuff: 52.63%
Jolteon: 57.69%
Jynx: 0.00%
Kabuto: 83.

...


Per-class accuracy:
Abra: 0.00%
Aerodactyl: 25.00%
Alakazam: 100.00%
Arbok: 63.64%
Arcanine: 11.11%
Articuno: 20.83%
Beedrill: 63.64%
Bellsprout: 82.61%
Blastoise: 50.00%
Bulbasaur: 48.15%
Butterfree: 90.00%
Caterpie: 36.84%
Chansey: 42.86%
Charizard: 41.18%
Charmander: 60.00%
Charmeleon: 0.00%
Clefable: 61.54%
Clefairy: 92.31%
Cloyster: 27.78%
Cubone: 0.00%
Dewgong: 42.86%
Diglett: 76.92%
Ditto: 91.67%
Dodrio: 58.33%
Doduo: 83.33%
Dragonair: 80.95%
Dragonite: 17.65%
Dratini: 41.18%
Drowzee: 11.11%
Dugtrio: 69.57%
Eevee: 52.63%
Ekans: 63.64%
Electabuzz: 62.50%
Electrode: 100.00%
Exeggcute: 88.89%
Exeggutor: 76.47%
Farfetch'd: 10.53%
Fearow: 50.00%
Flareon: 26.92%
Gastly: 80.00%
Gengar: 71.43%
Geodude: 33.33%
Gloom: 100.00%
Golbat: 50.00%
Goldeen: 0.00%
Golduck: 28.57%
Golem: 52.94%
Graveler: 42.86%
Grimer: 82.35%
Growlithe: 35.71%
Gyarados: 23.53%
Haunter: 70.59%
Hitmonchan: 15.38%
Hitmonlee: 28.57%
Horsea: 66.67%
Hypno: 75.00%
Ivysaur: 85.71%
Jigglypuff: 73.68%
Jolteon: 76.92%
Jynx: 

Training:   0%|          | 1/359 [00:02<15:48,  2.65s/it, loss=0.006, acc=43.75%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:   6%|▌         | 22/359 [00:44<11:47,  2.10s/it, loss=0.182, acc=45.31%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  42%|████▏     | 151/359 [05:12<06:49,  1.97s/it, loss=1.196, acc=45.90%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  91%|█████████▏| 328/359 [11:20<01:05,  2.12s/it, loss=2.685, acc=44.64%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.


Per-class accuracy:
Abra: 25.00%
Aerodactyl: 50.00%
Alakazam: 83.33%
Arbok: 81.82%
Arcanine: 66.67%
Articuno: 29.17%
Beedrill: 59.09%
Bellsprout: 73.91%
Blastoise: 16.67%
Bulbasaur: 40.74%
Butterfree: 90.00%
Caterpie: 21.05%
Chansey: 42.86%
Charizard: 35.29%
Charmander: 60.00%
Charmeleon: 3.70%
Clefable: 61.54%
Clefairy: 84.62%
Cloyster: 33.33%
Cubone: 0.00%
Dewgong: 21.43%
Diglett: 76.92%
Ditto: 83.33%
Dodrio: 75.00%
Doduo: 83.33%
Dragonair: 90.48%
Dragonite: 23.53%
Dratini: 47.06%
Drowzee: 22.22%
Dugtrio: 43.48%
Eevee: 57.89%
Ekans: 63.64%
Electabuzz: 62.50%
Electrode: 100.00%
Exeggcute: 66.67%
Exeggutor: 70.59%
Farfetch'd: 21.05%
Fearow: 58.33%
Flareon: 26.92%
Gastly: 60.00%
Gengar: 57.14%
Geodude: 33.33%
Gloom: 83.33%
Golbat: 41.67%
Goldeen: 16.67%
Golduck: 0.00%
Golem: 41.18%
Graveler: 50.00%
Grimer: 47.06%
Growlithe: 46.43%
Gyarados: 11.76%
Haunter: 82.35%
Hitmonchan: 7.69%
Hitmonlee: 0.00%
Horsea: 62.96%
Hypno: 50.00%
Ivysaur: 78.57%
Jigglypuff: 78.95%
Jolteon: 69.23%
Jynx: 100

Training:   1%|▏         | 5/359 [00:10<11:34,  1.96s/it, loss=0.036, acc=48.12%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:   5%|▌         | 18/359 [00:33<10:34,  1.86s/it, loss=0.134, acc=47.40%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:   7%|▋         | 24/359 [00:47<12:54,  2.31s/it, loss=0.179, acc=47.14%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Training:  14%|█▍        | 51/359 [02:07<15:09,  2.95s/it, loss=0.393, acc=47.00%]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py


Per-class accuracy:
Abra: 0.00%
Aerodactyl: 62.50%
Alakazam: 83.33%
Arbok: 63.64%
Arcanine: 11.11%
Articuno: 45.83%
Beedrill: 68.18%
Bellsprout: 78.26%
Blastoise: 75.00%
Bulbasaur: 59.26%
Butterfree: 86.67%
Caterpie: 21.05%
Chansey: 57.14%
Charizard: 5.88%
Charmander: 60.00%
Charmeleon: 0.00%
Clefable: 69.23%
Clefairy: 69.23%
Cloyster: 61.11%
Cubone: 8.33%
Dewgong: 28.57%
Diglett: 76.92%
Ditto: 83.33%
Dodrio: 66.67%
Doduo: 83.33%
Dragonair: 85.71%
Dragonite: 41.18%
Dratini: 47.06%
Drowzee: 77.78%
Dugtrio: 8.70%
Eevee: 57.89%
Ekans: 72.73%
Electabuzz: 62.50%
Electrode: 90.00%
Exeggcute: 77.78%
Exeggutor: 70.59%
Farfetch'd: 0.00%
Fearow: 58.33%
Flareon: 23.08%
Gastly: 60.00%
Gengar: 57.14%
Geodude: 41.67%
Gloom: 83.33%
Golbat: 50.00%
Goldeen: 0.00%
Golduck: 57.14%
Golem: 35.29%
Graveler: 42.86%
Grimer: 5.88%
Growlithe: 50.00%
Gyarados: 17.65%
Haunter: 76.47%
Hitmonchan: 30.77%
Hitmonlee: 35.71%
Horsea: 55.56%
Hypno: 100.00%
Ivysaur: 71.43%
Jigglypuff: 89.47%
Jolteon: 69.23%
Jynx: 50.00%

In [18]:

# Plot training history
plt.figure(figsize=(12, 4))

plt.subplot(1, 2, 1)
plt.plot(train_losses, label='Train Loss')
plt.plot(val_losses, label='Val Loss')
plt.title('Loss Over Time')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()

plt.subplot(1, 2, 2)
plt.plot(train_accs, label='Train Accuracy')
plt.plot(val_accs, label='Val Accuracy')
plt.title('Accuracy Over Time')
plt.xlabel('Epoch')
plt.ylabel('Accuracy (%)')
plt.legend()

plt.tight_layout()
plt.show()

In [19]:
# Load best model and evaluate on test set
print("\nEvaluating best model on test set...")
model.load_state_dict(torch.load("checkpoints/training_checkpoint.pth")['model_state_dict'])
test_loss, test_acc = validate(model, test_loader, criterion)
print(f"\nTest Loss: {test_loss:.4f}, Test Accuracy: {test_acc:.2f}%")

# Additional metrics
from sklearn.metrics import precision_recall_fscore_support

all_labels = []
all_preds = []

model.eval()
with torch.no_grad():
    for inputs, labels in tqdm(test_loader, desc="Testing"):
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = model(inputs)
        _, predicted = outputs.max(1)
        all_labels.extend(labels.cpu().numpy())
        all_preds.extend(predicted.cpu().numpy())

precision, recall, f1, _ = precision_recall_fscore_support(all_labels, all_preds, average=None, labels=range(num_classes))

print("\nPer-class metrics:")
for i, class_name in enumerate(full_dataset.classes):
    print(f"{class_name}:")
    print(f"  Precision: {precision[i]:.2f}")
    print(f"  Recall: {recall[i]:.2f}")
    print(f"  F1-score: {f1[i]:.2f}")

# Overall metrics
overall_precision, overall_recall, overall_f1, _ = precision_recall_fscore_support(all_labels, all_preds, average='weighted')
print("\nOverall metrics:")
print(f"  Precision: {overall_precision:.2f}")
print(f"  Recall: {overall_recall:.2f}")
print(f"  F1-score: {overall_f1:.2f}")


Evaluating best model on test set...


/tmp/ipykernel_106377/2852024671.py:3: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load("checkpoints/training_checkpoint.pth")['model_state_dic


Per-class accuracy:
Abra: 28.57%
Aerodactyl: 69.23%
Alakazam: 90.91%
Arbok: 65.22%
Arcanine: 31.25%
Articuno: 88.24%
Beedrill: 94.74%
Bellsprout: 73.68%
Blastoise: 65.00%
Bulbasaur: 64.29%
Butterfree: 79.17%
Caterpie: 54.55%
Chansey: 33.33%
Charizard: 15.38%
Charmander: 66.67%
Charmeleon: 0.00%
Clefable: 77.78%
Clefairy: 54.55%
Cloyster: 53.85%
Cubone: 6.67%
Dewgong: 35.29%
Diglett: 85.71%
Ditto: 80.00%
Dodrio: 54.55%
Doduo: 62.50%
Dragonair: 80.00%
Dragonite: 72.22%
Dratini: 25.00%
Drowzee: 60.00%
Dugtrio: 11.76%
Eevee: 60.00%
Ekans: 81.25%
Electabuzz: 26.67%
Electrode: 77.78%
Exeggcute: 94.12%
Exeggutor: 50.00%
Farfetch'd: 5.26%
Fearow: 64.29%
Flareon: 20.00%
Gastly: 70.00%
Gengar: 50.00%
Geodude: 26.67%
Gloom: 92.31%
Golbat: 80.00%
Goldeen: 0.00%
Golduck: 61.90%
Golem: 26.67%
Graveler: 41.18%
Grimer: 0.00%
Growlithe: 72.22%
Gyarados: 25.00%
Haunter: 50.00%
Hitmonchan: 22.22%
Hitmonlee: 35.29%
Horsea: 58.82%
Hypno: 63.64%
Ivysaur: 70.00%
Jigglypuff: 95.24%
Jolteon: 52.94%
Jynx: 85.7

Testing:  27%|██▋       | 21/77 [00:30<01:27,  1.57s/it]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Testing:  78%|███████▊  | 60/77 [01:31<00:26,  1.58s/it]/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(
Testing: 100%|██████████| 77/77 [01:56<00:00,  1.52s/it]


Per-class metrics:
Abra:
  Precision: 0.15
  Recall: 0.29
  F1-score: 0.20
Aerodactyl:
  Precision: 0.64
  Recall: 0.69
  F1-score: 0.67
Alakazam:
  Precision: 0.25
  Recall: 0.91
  F1-score: 0.39
Arbok:
  Precision: 1.00
  Recall: 0.65
  F1-score: 0.79
Arcanine:
  Precision: 0.83
  Recall: 0.31
  F1-score: 0.45
Articuno:
  Precision: 0.94
  Recall: 0.88
  F1-score: 0.91
Beedrill:
  Precision: 0.67
  Recall: 0.95
  F1-score: 0.78
Bellsprout:
  Precision: 0.93
  Recall: 0.74
  F1-score: 0.82
Blastoise:
  Precision: 0.35
  Recall: 0.65
  F1-score: 0.46
Bulbasaur:
  Precision: 1.00
  Recall: 0.64
  F1-score: 0.78
Butterfree:
  Precision: 1.00
  Recall: 0.79
  F1-score: 0.88
Caterpie:
  Precision: 1.00
  Recall: 0.55
  F1-score: 0.71
Chansey:
  Precision: 1.00
  Recall: 0.33
  F1-score: 0.50
Charizard:
  Precision: 0.50
  Recall: 0.15
  F1-score: 0.24
Charmander:
  Precision: 1.00
  Recall: 0.67
  F1-score: 0.80
Charmeleon:
  Precision: 0.00
  Recall: 0.00
  F1-score: 0.00
Clefable:
  Pre


/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/jules/.pyenv/versions/3.11.5/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [20]:
from PIL import Image

def predict_pokemon(model, image_path, ax=None):
    model.eval()
    true_label = Path(image_path).parent.name
    
    # Load image
    image = Image.open(image_path).convert('RGB')
    
    # Handle plotting
    if ax is None:
        fig, ax = plt.subplots(figsize=(4, 4))
    ax.imshow(image)
    ax.axis('off')
    
    # Make prediction
    image_tensor = val_test_transforms(image).unsqueeze(0).to(device)
    with torch.no_grad():
        output = model(image_tensor)
        _, predicted = output.max(1)
    
    prediction = full_dataset.classes[predicted.item()]
    is_correct = prediction == true_label
    color = 'green' if is_correct else 'red'
    
    ax.set_title(f'{true_label}\n→ {prediction}', 
                 color=color, 
                 fontsize=10)
    
    return prediction

def predict_random_samples(model, num_samples=9):
    # Get random indices
    indices = torch.randperm(len(test_dataset))[:num_samples]
    
    # Create subplot grid
    rows = int(np.ceil(np.sqrt(num_samples)))
    cols = int(np.ceil(num_samples / rows))
    fig, axes = plt.subplots(rows, cols, figsize=(cols*4, rows*4))
    axes = axes.ravel()
    
    # Make predictions
    for idx, ax in zip(indices, axes):
        # Get image path from dataset
        image_path = test_dataset.dataset.samples[test_dataset.indices[idx]][0]
        predict_pokemon(model, image_path, ax)
        
    # Hide empty subplots if any
    for idx in range(num_samples, len(axes)):
        axes[idx].axis('off')
    
    plt.tight_layout()
    plt.show()

In [21]:
predict_random_samples(model, 25)